# Feature Importance Permutation Testing Visualization and Analysis


## Imports

In [9]:
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from IPython.display import Image
import os
import numpy as np
import pandas as pd
import datetime as dt

## Read in Data

In [10]:
# fi_df = pd.read_csv("FeatureImportance_Results_indexed.csv")
fi_df = pd.read_csv("FeatureImportance_followup_indexed_renamed.csv")
fi_df['Label2'].unique()

array(['Visual', 'Somatomotor', 'Dorsal Attention',
       'Salience / Ventral Attention', 'Limbic', 'Control', 'Default',
       'Random', 'Vis_Vis', 'Vis_SomMot', 'Vis_DorsAttn',
       'Vis_SalVentAttn', 'Vis_Limbic', 'Vis_Cont', 'Vis_Default',
       'SomMot_SomMot', 'SomMot_DorsAttn', 'SomMot_SalVentAttn',
       'SomMot_Limbic', 'SomMot_Cont', 'SomMot_Default',
       'DorsAttn_DorsAttn', 'DorsAttn_SalVentAttn', 'DorsAttn_Limbic',
       'DorsAttn_Cont', 'DorsAttn_Default', 'SalVentAttn_SalVentAttn',
       'SalVentAttn_Limbic', 'SalVentAttn_Cont', 'SalVentAttn_Default',
       'Limbic_Limbic', 'Limbic_Cont', 'Limbic_Default', 'Cont_Cont',
       'Cont_Default', 'Default_Default'], dtype=object)

## SetUp Color Mappings

In [16]:
size_index_df = pd.read_csv('FeatureImportance_index_renamed.csv')
size_index_df = size_index_df[~size_index_df['Label'].str.contains('Rand')]
size_index_df = size_index_df[
  ~(size_index_df['Label'].str.contains('_')) &
  ~(size_index_df['Label'].str.contains('-'))
]
size_index_df.reset_index(inplace=True,drop=True)
size_index_df

NumberPermuted                         Label
0            2322                        Limbic
1            4147  Salience / Ventral Attention
2            4849              Dorsal Attention
3            5365                        Visual
4            5535                       Control
5            6370                   Somatomotor
6            8119                       Default

In [17]:

n_colors = len(size_index_df)#len(fi_df['Label2'].unique())
colors = px.colors.sample_colorscale("turbo", [n/(n_colors -1) for n in range(n_colors)])
colors

['rgb(48, 18, 59)',
 'rgb(66, 132, 242)',
 'rgb(33, 226, 181)',
 'rgb(164, 252, 59)',
 'rgb(247, 184, 54)',
 'rgb(226, 70, 11)',
 'rgb(122, 4, 2)']

In [18]:


target_dict = {}
color_ind = 1
for index, row in size_index_df.iterrows():
  print(color_ind)
  target_dict[row['Label']] = {
    'NumberPermuted':row['NumberPermuted'],
    'color':colors[color_ind-1]
  }
  color_ind+=1

target_dict.keys()

1
2
3
4
5
6
7


dict_keys(['Limbic', 'Salience / Ventral Attention', 'Dorsal Attention', 'Visual', 'Control', 'Somatomotor', 'Default'])

In [19]:

fig = go.Figure()
# for i, c in enumerate(greys15):
for i, c in enumerate(colors):
  # print(i,c)
  fig.add_bar(x=[i], y = [15], marker_color = c, showlegend = False, name=c)
f = fig.full_figure_for_development(warn=False)
fig.show()
len(list(target_dict.keys()))

7

In [20]:
# outcomes = [
#   "ADHD|PredictedADHD_percent","ADHD|PredictedBIPOLAR_percent","ADHD|PredictedSCHZ_percent",
#   "BIPOLAR|PredictedADHD_percent","BIPOLAR|PredictedBIPOLAR_percent","BIPOLAR|PredictedSCHZ_percent",
#   "SCHZ|PredictedADHD_percent","SCHZ|PredictedBIPOLAR_percent","SCHZ|PredictedSCHZ_percent"
# ]
diag_list = ['SCZ','BD','ADHD']

arr_plot = make_subplots(
  rows = 3,
  cols = 3,
  row_titles=diag_list,
  column_titles=diag_list,
  x_title='Predicted',
  y_title='True'
)
network_list = [
  'Limbic',
  'Salience / Ventral Attention',
  'Dorsal Attention',
  'Visual',
  'Control',
  'Somatomotor',
  'Default'
]
ind = 0
ind_b = 0
for i in diag_list:
  for j in diag_list:
    outcome = f'{i}|Predicted{j}_percent'
    for subset in list(target_dict.keys())[:]:
      sub_df = fi_df[fi_df['N_Permuted']==list(fi_df[fi_df['Label2']==subset]['N_Permuted'])[0]]
      sub_df['N_Permuted'] = sub_df['N_Permuted'].astype(str)
      sub_df['xlab'] = subset
      #Add the random Trace
      if ind==0:
        arr_plot.add_trace(go.Violin(
            x=sub_df[sub_df['Label2']=='Random']["xlab"],
            y=sub_df[sub_df['Label2']=='Random'][outcome],
            legendgroup='Random',
            scalegroup='Random',
            name=f'Random',
            line_color='black',
            showlegend=True,
            side='negative'
          ), 
          row = diag_list.index(i)+1,
          col = diag_list.index(j)+1
        )
      else:
        arr_plot.add_trace(go.Violin(
            x=sub_df[sub_df['Label2']=='Random']["xlab"],
            y=sub_df[sub_df['Label2']=='Random'][outcome],
            name=f'Random',
            line_color='black',
            showlegend=False,
            side='negative'
          ), 
          row = diag_list.index(i)+1,
          col = diag_list.index(j)+1
        )
      if ind_b == 0:
        # Add the target trace
        arr_plot.add_trace(
          go.Violin(
            x=sub_df[sub_df['Label2']==subset]["xlab"],
            y=sub_df[sub_df['Label2']==subset][outcome],
            legendgroup=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            scalegroup=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            name=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            line_color=target_dict[subset]['color'],
            showlegend=True,
            side='positive'
          ), 
          row = diag_list.index(i)+1,
          col = diag_list.index(j)+1
        )
      else:
        # Add the target trace
        arr_plot.add_trace(
          go.Violin(
            x=sub_df[sub_df['Label2']==subset]["xlab"],
            y=sub_df[sub_df['Label2']==subset][outcome],
            legendgroup=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            scalegroup=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            name=f'{subset} ({list(sub_df["N_Permuted"])[0]})',
            line_color=target_dict[subset]['color'],
            showlegend=False,
            side='positive'
          ), 
          row = diag_list.index(i)+1,
          col = diag_list.index(j)+1
        )
      ind+=1
    ind_b+=1
      

arr_plot.update_layout(
  # height=800, 
  # width=1000, 
  # title_text=f'Network Connection Feature Importance',
  showlegend=True,
  font=dict(
    # family="Times New Roman",
    size=10,
    color="White"
    ),
  template='plotly_dark',
  paper_bgcolor='White',
  plot_bgcolor='White'
)
arr_plot.update_yaxes(range = [0,1])
arr_plot.update_traces({
  'line':{
    'width':0
  },
  'marker':{
    'color':'rgba(0,0,0,0)'
  },
  'box':{
    'width':1
  },
  'meanline':{
    'visible':True,
    'color':'white',
    'width':2
  }
})
arr_plot.update_xaxes(showticklabels=False)
arr_plot.for_each_annotation(
  lambda a:  a.update(x = 0,textangle=-90, xanchor='right', xshift=-40) if a.x ==.98 else
  a.update(xshift = -60) if a.x ==0 else
  a.update(yanchor = 'bottom', y=1,yshift = 25) if a.text == "Predicted" else()
  # a.update(x = -0.07) if a.text in row_titles else()
)
arr_plot.update_layout(margin=dict(t = 60, l = 120))
arr_plot.write_html('FeatureImportance_Results_02a.html')
arr_plot.update_layout(
    font=dict(
      # family="Times New Roman",
      # size=35,
      color="Black"
      ),
  )
arr_plot.write_image('FeatureImportance_Results_02b.png')
arr_plot.show()